# **Construção de um Pipeline de Dados Simples para Análise de Logs de Servidor Web**

## **Contexto**
Os logs de servidor da Web contêm informações sobre qualquer evento que foi registrado/registrado. Isso contém muitos insights sobre visitantes do site, comportamento, rastreadores que acessam o site, insights de negócios, problemas de segurança e muito mais.

Este é um conjunto de dados para tentar obter insights desse arquivo.

In [1]:
'''
OBs: Um pipeline de dados é uma sequência de etapas interconectadas que permitem a coleta, armazenamento, transformação, análise e visualização de dados
'''
import locale
import pandas as pd
import numpy as np
from sqlalchemy import create_engine
import requests
import re
from urllib.parse import urlparse, quote, unquote
from user_agents import parse
import sqlite3

In [2]:
pd.set_option('display.max_columns', None)

## **1. Exctração**

In [3]:
def extract(file, tamanho):
    with open (file,'r') as archive:
        return archive.read(tamanho) 

In [4]:
tamanho =8500000#
arquivo = extract('access.log', tamanho)
print(arquivo) # printando os arquivos
print(f'\n\nA quantidade de caracteres que forma lidos -> {float(len(arquivo))}')

54.36.149.41 - - [22/Jan/2019:03:56:14 +0330] "GET /filter/27|13%20%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%DA%A9%D8%B3%D9%84,27|%DA%A9%D9%85%D8%AA%D8%B1%20%D8%A7%D8%B2%205%20%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%DA%A9%D8%B3%D9%84,p53 HTTP/1.1" 200 30577 "-" "Mozilla/5.0 (compatible; AhrefsBot/6.1; +http://ahrefs.com/robot/)" "-"
31.56.96.51 - - [22/Jan/2019:03:56:16 +0330] "GET /image/60844/productModel/200x200 HTTP/1.1" 200 5667 "https://www.zanbil.ir/m/filter/b113" "Mozilla/5.0 (Linux; Android 6.0; ALE-L21 Build/HuaweiALE-L21) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/66.0.3359.158 Mobile Safari/537.36" "-"
31.56.96.51 - - [22/Jan/2019:03:56:16 +0330] "GET /image/61474/productModel/200x200 HTTP/1.1" 200 5379 "https://www.zanbil.ir/m/filter/b113" "Mozilla/5.0 (Linux; Android 6.0; ALE-L21 Build/HuaweiALE-L21) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/66.0.3359.158 Mobile Safari/537.36" "-"
40.77.167.129 - - [22/Jan/2019:03:56:17 +0330] "GET /image/14925/productModel/100x100 HTTP/1.1" 200 1696 

# **2. o que tem neste arquivo log?**
- ***IP***: 54.36.149.41

- ***Data***: 22/Jan/2019:03:56:14 +0330
- ***Método***: GET
- ***URL***: /filter/27|13%20%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%DA%A9%D8%B3%D9%84
- ***Protocolo***: HTTP/1.1
- ***Status***: 200
- ***Tamanho***: 30577
- ***User***-Agent: Mozilla/5.0 (compatible; AhrefsBot/6.1; +http://ahrefs.com/robot/)

# **3. Transformação**

In [5]:
def convert_pd(data_extract): # Mandando os dados para ser tranformados e organizados no pandas

    logpadrao = r'''(\d+\.\d+\d+\.\d+\.\d+) - - \[([^\]]+)\] "(\w+) ([^"]+) ([^"]+)" (\d+) (\d+) "-" "([^"]+)'''
    resultado = re.finditer(logpadrao, data_extract)
    data_convert = [
        {
                'Ip': res.group(1), # pegando o endereco IP
                'Date': res.group(2), # pegando a Data
                'Methode':res.group(3), # pegando o Metodo
                'URL': res.group(4), # pegando a URL
                'Protocol': res.group(5), # pegando o protrocolo
                'Status': int(res.group(6)), # Pegando status
                'Size': int(res.group(7)),# Tamanho
                'User-Agent': res.group(8) # Angente usuario ex.: Bot ou robos
        }  
        for res in resultado
    ]   
    return pd.DataFrame(data_convert)

In [6]:
df = convert_pd(arquivo)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15453 entries, 0 to 15452
Data columns (total 8 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   Ip          15453 non-null  object
 1   Date        15453 non-null  object
 2   Methode     15453 non-null  object
 3   URL         15453 non-null  object
 4   Protocol    15453 non-null  object
 5   Status      15453 non-null  int64 
 6   Size        15453 non-null  int64 
 7   User-Agent  15453 non-null  object
dtypes: int64(2), object(6)
memory usage: 965.9+ KB


#  **2. Padronização de formatos**
## ***2.1. Formatando o tempo***

In [7]:
df['Date'] = pd.to_datetime(df['Date'], format="%d/%b/%Y:%H:%M:%S %z").dt.tz_localize(None)# formatação do tempo
df.Date.astype(str)
df.head() # 

Ip                Date Methode  \
0   54.36.149.41 2019-01-22 03:56:14     GET   
1  40.77.167.129 2019-01-22 03:56:17     GET   
2    91.99.72.15 2019-01-22 03:56:17     GET   
3  40.77.167.129 2019-01-22 03:56:17     GET   
4  40.77.167.129 2019-01-22 03:56:18     GET   

                                                 URL  Protocol  Status   Size  \
0  /filter/27|13%20%D9%85%DA%AF%D8%A7%D9%BE%DB%8C...  HTTP/1.1     200  30577   
1                  /image/14925/productModel/100x100  HTTP/1.1     200   1696   
2  /product/31893/62100/%D8%B3%D8%B4%D9%88%D8%A7%...  HTTP/1.1     200  41483   
3                  /image/23488/productModel/150x150  HTTP/1.1     200   2654   
4                  /image/45437/productModel/150x150  HTTP/1.1     200   3688   

                                          User-Agent  
0  Mozilla/5.0 (compatible; AhrefsBot/6.1; +http:...  
1  Mozilla/5.0 (compatible; bingbot/2.0; +http://...  
2  Mozilla/5.0 (Windows NT 6.2; Win64; x64; rv:16...  
3  Mozilla/5.0 (compatible; bingbot/2.0; +http://...  
4  Mozilla/5.0 (compatible; bingbot/2.0; +http://...

In [8]:
df.info() # vendo se o tempo foi formatado

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 15453 entries, 0 to 15452
Data columns (total 8 columns):
 #   Column      Non-Null Count  Dtype         
---  ------      --------------  -----         
 0   Ip          15453 non-null  object        
 1   Date        15453 non-null  datetime64[ns]
 2   Methode     15453 non-null  object        
 3   URL         15453 non-null  object        
 4   Protocol    15453 non-null  object        
 5   Status      15453 non-null  int64         
 6   Size        15453 non-null  int64         
 7   User-Agent  15453 non-null  object        
dtypes: datetime64[ns](1), int64(2), object(5)
memory usage: 965.9+ KB


# **3. Remoção de duplicidades e erros**

In [9]:
df = df.drop_duplicates() # apagando os dados duplicados

In [10]:
df.isna().sum() # verificando se há dados faltantes

Ip            0
Date          0
Methode       0
URL           0
Protocol      0
Status        0
Size          0
User-Agent    0
dtype: int64

## **4. Padronizando os métodos**

In [11]:
# 2 - Padronização de métodos HTTP: Deixar todos os métodos (GET, POST, etc.) em maiúsculas.
df.Methode.str.upper().head(2) # get GET gET

0    GET
1    GET
Name: Methode, dtype: object

# **5. Fazer a limpeza da URL**

* Decodificar caracteres especiais.
* Remover parâmetros irrelevantes (utm, sessionid, etc.).
* Remover barras finais redundantes.
* Padronizar domínio e esquema para minúsculas.

In [12]:
def limparURL(url: str) -> str:
    # validação ----------
    if not isinstance(url, str) or not url.strip():
        return ''

    # ---------- decode ----------
    decoded = unquote(url.strip())

    # ---------- parse ----------
    parsed = urlparse(decoded)

    path = parsed.path or ''

    # ---------- normalizações estruturais ----------
    path = re.sub(r'/+', '/', path)           # múltiplas barras → 1
    path = path.rstrip('/')                   # remove trailing slash
    path = path.replace('|', '-')             # separador consistente
    path = re.sub(r'\s+', '-', path)          # espaços → hífen
    path = re.sub(r'-+', '-', path)           # colapsa hífens

    # remove caracteres inválidos mas mantém unicode válido
    path = re.sub(r'[^\w\-/\u0080-\uFFFF]', '', path)

    path = path.strip('-').lower()

    #  canonical encoding 
    path = quote(path, safe="/-")

    return path


# aplicar dataframe
df["URL"] = df["URL"].apply(limparURL)

df['URL'].head(20)

0     /filter/27-13-%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%D...
1                     /image/14925/productmodel/100x100
2     /product/31893/62100/%D8%B3%D8%B4%D9%88%D8%A7%...
3                     /image/23488/productmodel/150x150
4                     /image/45437/productmodel/150x150
5                            /image/576/article/100x100
6     /filter/b41b665c150-%D8%A8%D8%AE%D8%A7%D8%B1%D...
7                     /image/57710/productmodel/100x100
8                                        /product/10214
9                            /image/578/article/100x100
10                     /image/6229/productmodel/100x100
11    /product/10075/13903/%D9%85%D8%A7%DB%8C%DA%A9%...
12                     /image/6229/productmodel/150x150
13                                       /product/14926
14                     /image/6248/productmodel/150x150
15                    /image/64815/productmodel/150x150
16                                       /m/filter/b2p6
17    /product/32798/63266/%DB%8C%D8%AE%DA%86%D8

In [13]:
url = df.URL
url[url.isnull() == True] = '/'
df.URL = url

/tmp/ipykernel_58187/1513873738.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  url[url.isnull() == True] = '/'


In [14]:
df =  df[['Ip', 'Date', 'Methode', 'URL', 'Protocol', 'Status', 'Size','User-Agent']]
df.head(3)

Ip                Date Methode  \
0   54.36.149.41 2019-01-22 03:56:14     GET   
1  40.77.167.129 2019-01-22 03:56:17     GET   
2    91.99.72.15 2019-01-22 03:56:17     GET   

                                                 URL  Protocol  Status   Size  \
0  /filter/27-13-%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%D...  HTTP/1.1     200  30577   
1                  /image/14925/productmodel/100x100  HTTP/1.1     200   1696   
2  /product/31893/62100/%D8%B3%D8%B4%D9%88%D8%A7%...  HTTP/1.1     200  41483   

                                          User-Agent  
0  Mozilla/5.0 (compatible; AhrefsBot/6.1; +http:...  
1  Mozilla/5.0 (compatible; bingbot/2.0; +http://...  
2  Mozilla/5.0 (Windows NT 6.2; Win64; x64; rv:16...

# **6 - Normalizar os User-Agent**
**User-Agent:** São as infromacões que o cliente (navegador ou app) envia num servidor 
quando faz a requisicao.
O que importa no user-agent:
"""
1. **Cliente/Navegador** {
    * Chrome
    * Firefox
    * Safari
    * Edge
    * Bots (Googlebot, Bingbot, etc.) - é um cliente
    * Apps (curl, python-requests…) - é um cliente
    
}

2. **Versao do navegador** {
    * Chrome 122
    * Firefox 115
     
}

3. **Sistema operativo** {
    * Windows 10/11
    * Android 13
    * iOS 17
    * Linux
     
}

4. **Tipo de dispositivo** {
    * Desktop
    * Mobile
    * Tablet
    * Smart TV
    * Bot / Crawler
}
5. **Motor do browser** {
    * Blink
    * WebKit
    * Gecko

}


In [15]:
# Formatação dos user-agentes
def user_agents(ua_string):
    ua = parse(ua_string)
    return pd.Series({
        "browser": ua.browser.family, # o tipo de navegador
        "browser_version": ua.browser.version_string, # versao do navegador
        "os": ua.os.family, # verificando o tipo de sistema operacional
        "os_version": ua.os.version_string, # a versao do sistema operacional
        "device": ua.device.family, # O despositivo
        "is_mobile": ua.is_mobile, # é despositivo movel
        "is_tablet": ua.is_tablet,
        "is_pc": ua.is_pc,
        "is_bot": ua.is_bot
    })

df_parced = df['User-Agent'].apply(user_agents)
df = pd.concat([df,df_parced], axis = 1)
df.drop(columns = 'User-Agent', inplace = True)
df.head()

Ip                Date Methode  \
0   54.36.149.41 2019-01-22 03:56:14     GET   
1  40.77.167.129 2019-01-22 03:56:17     GET   
2    91.99.72.15 2019-01-22 03:56:17     GET   
3  40.77.167.129 2019-01-22 03:56:17     GET   
4  40.77.167.129 2019-01-22 03:56:18     GET   

                                                 URL  Protocol  Status   Size  \
0  /filter/27-13-%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%D...  HTTP/1.1     200  30577   
1                  /image/14925/productmodel/100x100  HTTP/1.1     200   1696   
2  /product/31893/62100/%D8%B3%D8%B4%D9%88%D8%A7%...  HTTP/1.1     200  41483   
3                  /image/23488/productmodel/150x150  HTTP/1.1     200   2654   
4                  /image/45437/productmodel/150x150  HTTP/1.1     200   3688   

     browser browser_version       os os_version  device  is_mobile  \
0  AhrefsBot             6.1    Other             Spider      False   
1    bingbot             2.0    Other             Spider      False   
2    Firefox            16.0  Windows          8   Other      False   
3    bingbot             2.0    Other             Spider      False   
4    bingbot             2.0    Other             Spider      False   

   is_tablet  is_pc  is_bot  
0      False  False    True  
1      False  False    True  
2      False   True   False  
3      False  False    True  
4      False  False    True

# **7 - Enriquecer os dados** 
## **7.1 Geolocalizar endereços IP**

In [16]:
# Para que nao haja problemas criei uma copia do dataset
df_original = df.copy()

In [17]:
# Caso há
ips_unicos = (
    df_original["Ip"]
    .dropna()
    .astype(str)
    .unique()
)
ips_unicos.size

846

In [18]:
ips = ips_unicos
dados_ips = ips.tolist() # conrtendo para lista
# dados_ips

In [19]:
format_ip = []
for IP in dados_ips:
    try:
        r = requests.get(f'http://ip-api.com/json/{IP}?fields=status,message,continent,continentCode,country,countryCode,region,regionName,city,district,zip,lat,lon,timezone,isp,org,as,asname,reverse,mobile,proxy,hosting,query',
            timeout=15
        )

        if r.status_code != 200:
            print("Erro HTTP:", r.status_code, r.text)
            continue

        if "application/json" not in r.headers.get("Content-Type",""):
            print("Resposta não JSON:", r.text)
            continue
        elif r.status_code == 200:
            print(r.json())
        format_ip.append(r.json())

    except requests.RequestException as e:
        print("Erro de requisição:", e)

{'status': 'success', 'continent': 'Europe', 'continentCode': 'EU', 'country': 'France', 'countryCode': 'FR', 'region': 'HDF', 'regionName': 'Hauts-de-France', 'city': 'Roubaix', 'district': '', 'zip': '59100', 'lat': 50.6924, 'lon': 3.20113, 'timezone': 'Europe/Paris', 'isp': 'OVH SAS', 'org': 'OVH', 'as': 'AS16276 OVH SAS', 'asname': 'OVH', 'reverse': 'hydrogen297-ext2.ahrefs.net', 'mobile': False, 'proxy': False, 'hosting': True, 'query': '54.36.149.41'}
{'status': 'success', 'continent': 'North America', 'continentCode': 'NA', 'country': 'United States', 'countryCode': 'US', 'region': 'VA', 'regionName': 'Virginia', 'city': 'Boydton', 'district': '', 'zip': '23917', 'lat': 36.677696, 'lon': -78.37471, 'timezone': 'America/New_York', 'isp': 'Microsoft Corporation', 'org': 'Microsoft Azure Cloud (eastus2)', 'as': 'AS8075 Microsoft Corporation', 'asname': 'MICROSOFT-CORP-MSN-AS-BLOCK', 'reverse': 'msnbot-40-77-167-129.search.msn.com', 'mobile': False, 'proxy': False, 'hosting': True, 

In [20]:
len(format_ip)

846

In [42]:
ip_geo = pd.DataFrame(format_ip)
# ip_geo = pd.read_csv('Ips2.csv')
ip_geo.columns

Index(['status', 'continent', 'continentCode', 'country', 'countryCode',
       'region', 'regionName', 'city', 'district', 'zip', 'lat', 'lon',
       'timezone', 'isp', 'org', 'as', 'asname', 'reverse', 'mobile', 'proxy',
       'hosting', 'query', 'message'],
      dtype='object')

In [ ]:
ip_geo.to_csv('Ips.csv')

In [23]:
ip_geo.isnull().sum()

status             0
continent          1
continentCode      1
country            1
countryCode        1
region             1
regionName         1
city               1
district           1
zip                1
lat                1
lon                1
timezone           1
isp                1
org                1
as                 1
asname             1
reverse            1
mobile             1
proxy              1
hosting            1
query              0
message          845
dtype: int64

In [24]:
df_final = df_original.merge(ip_geo, left_on='Ip', right_on='query', how = 'left')


In [25]:
df_final.head()

Ip                Date Methode  \
0   54.36.149.41 2019-01-22 03:56:14     GET   
1  40.77.167.129 2019-01-22 03:56:17     GET   
2    91.99.72.15 2019-01-22 03:56:17     GET   
3  40.77.167.129 2019-01-22 03:56:17     GET   
4  40.77.167.129 2019-01-22 03:56:18     GET   

                                                 URL  Protocol  Status   Size  \
0  /filter/27-13-%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%D...  HTTP/1.1     200  30577   
1                  /image/14925/productmodel/100x100  HTTP/1.1     200   1696   
2  /product/31893/62100/%D8%B3%D8%B4%D9%88%D8%A7%...  HTTP/1.1     200  41483   
3                  /image/23488/productmodel/150x150  HTTP/1.1     200   2654   
4                  /image/45437/productmodel/150x150  HTTP/1.1     200   3688   

     browser browser_version       os os_version  device  is_mobile  \
0  AhrefsBot             6.1    Other             Spider      False   
1    bingbot             2.0    Other             Spider      False   
2    Firefox            16.0  Windows          8   Other      False   
3    bingbot             2.0    Other             Spider      False   
4    bingbot             2.0    Other             Spider      False   

   is_tablet  is_pc  is_bot   status      continent continentCode  \
0      False  False    True  success         Europe            EU   
1      False  False    True  success  North America            NA   
2      False   True   False  success         Europe            EU   
3      False  False    True  success  North America            NA   
4      False  False    True  success  North America            NA   

         country countryCode region       regionName       city district  \
0         France          FR    HDF  Hauts-de-France    Roubaix            
1  United States          US     VA         Virginia    Boydton            
2        Germany          DE     BY          Bavaria  Nuremberg            
3  United States          US     VA         Virginia    Boydton            
4  United States          US     VA         Virginia    Boydton            

     zip        lat       lon          timezone                    isp  \
0  59100  50.692400   3.20113      Europe/Paris                OVH SAS   
1  23917  36.677696 -78.37471  America/New_York  Microsoft Corporation   
2  90403  49.452700  11.07830     Europe/Berlin    Hetzner Online GmbH   
3  23917  36.677696 -78.37471  America/New_York  Microsoft Corporation   
4  23917  36.677696 -78.37471  America/New_York  Microsoft Corporation   

                               org                            as  \
0                              OVH               AS16276 OVH SAS   
1  Microsoft Azure Cloud (eastus2)  AS8075 Microsoft Corporation   
2                          Hetzner   AS24940 Hetzner Online GmbH   
3  Microsoft Azure Cloud (eastus2)  AS8075 Microsoft Corporation   
4  Microsoft Azure Cloud (eastus2)  AS8075 Microsoft Corporation   

                        asname                                    reverse  \
0                          OVH                hydrogen297-ext2.ahrefs.net   
1  MICROSOFT-CORP-MSN-AS-BLOCK        msnbot-40-77-167-129.search.msn.com   
2                   HETZNER-AS  static.15.72.99.91.clients.your-server.de   
3  MICROSOFT-CORP-MSN-AS-BLOCK        msnbot-40-77-167-129.search.msn.com   
4  MICROSOFT-CORP-MSN-AS-BLOCK        msnbot-40-77-167-129.search.msn.com   

  mobile  proxy hosting          query message  
0  False  False    True   54.36.149.41     NaN  
1  False  False    True  40.77.167.129     NaN  
2  False  False    True    91.99.72.15     NaN  
3  False  False    True  40.77.167.129     NaN  
4  False  False    True  40.77.167.129     NaN

In [26]:
df_final.isnull().sum()

Ip                     0
Date                   0
Methode                0
URL                    0
Protocol               0
Status                 0
Size                   0
browser                0
browser_version        0
os                     0
os_version             0
device                 0
is_mobile              0
is_tablet              0
is_pc                  0
is_bot                 0
status                 0
continent            181
continentCode        181
country              181
countryCode          181
region               181
regionName           181
city                 181
district             181
zip                  181
lat                  181
lon                  181
timezone             181
isp                  181
org                  181
as                   181
asname               181
reverse              181
mobile               181
proxy                181
hosting              181
query                  0
message            15249
dtype: int64

In [27]:
df_final.columns

Index(['Ip', 'Date', 'Methode', 'URL', 'Protocol', 'Status', 'Size', 'browser',
       'browser_version', 'os', 'os_version', 'device', 'is_mobile',
       'is_tablet', 'is_pc', 'is_bot', 'status', 'continent', 'continentCode',
       'country', 'countryCode', 'region', 'regionName', 'city', 'district',
       'zip', 'lat', 'lon', 'timezone', 'isp', 'org', 'as', 'asname',
       'reverse', 'mobile', 'proxy', 'hosting', 'query', 'message'],
      dtype='object')

In [28]:
# Organizando as colunas e pegando tabelas essencial para a análise
df_final = df_final[['Ip', 'Date', 'Methode', 'URL', 'Protocol', 'Status', 'is_mobile',
       'is_tablet', 'is_pc', 'is_bot', 'browser', 'os','continent','country', 'countryCode', 'regionName', 'city', 'lat', 'lon',
       'isp', 'org', 'as', 'proxy',
       'hosting', 'query']]

In [29]:
df_final.columns

Index(['Ip', 'Date', 'Methode', 'URL', 'Protocol', 'Status', 'is_mobile',
       'is_tablet', 'is_pc', 'is_bot', 'browser', 'os', 'continent', 'country',
       'countryCode', 'regionName', 'city', 'lat', 'lon', 'isp', 'org', 'as',
       'proxy', 'hosting', 'query'],
      dtype='object')

In [30]:
df_final.isnull().sum()

Ip               0
Date             0
Methode          0
URL              0
Protocol         0
Status           0
is_mobile        0
is_tablet        0
is_pc            0
is_bot           0
browser          0
os               0
continent      181
country        181
countryCode    181
regionName     181
city           181
lat            181
lon            181
isp            181
org            181
as             181
proxy          181
hosting        181
query            0
dtype: int64

In [31]:
df_final.org = df_final.org.fillna('Not Found')

In [32]:
df_final.dropna(subset = [
       'country', 'lat','lon', 'city', 'as', 'countryCode',
       'regionName', 'isp'],inplace = True)

In [33]:
df_final.isnull().sum()

Ip             0
Date           0
Methode        0
URL            0
Protocol       0
Status         0
is_mobile      0
is_tablet      0
is_pc          0
is_bot         0
browser        0
os             0
continent      0
country        0
countryCode    0
regionName     0
city           0
lat            0
lon            0
isp            0
org            0
as             0
proxy          0
hosting        0
query          0
dtype: int64

In [34]:
df_final.columns

Index(['Ip', 'Date', 'Methode', 'URL', 'Protocol', 'Status', 'is_mobile',
       'is_tablet', 'is_pc', 'is_bot', 'browser', 'os', 'continent', 'country',
       'countryCode', 'regionName', 'city', 'lat', 'lon', 'isp', 'org', 'as',
       'proxy', 'hosting', 'query'],
      dtype='object')

In [35]:
df_final.proxy = df_final.proxy.astype(bool)
df_final.hosting = df_final.hosting.astype(bool)


In [36]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Index: 15249 entries, 0 to 15429
Data columns (total 25 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   Ip           15249 non-null  object        
 1   Date         15249 non-null  datetime64[ns]
 2   Methode      15249 non-null  object        
 3   URL          15249 non-null  object        
 4   Protocol     15249 non-null  object        
 5   Status       15249 non-null  int64         
 6   is_mobile    15249 non-null  bool          
 7   is_tablet    15249 non-null  bool          
 8   is_pc        15249 non-null  bool          
 9   is_bot       15249 non-null  bool          
 10  browser      15249 non-null  object        
 11  os           15249 non-null  object        
 12  continent    15249 non-null  object        
 13  country      15249 non-null  object        
 14  countryCode  15249 non-null  object        
 15  regionName   15249 non-null  object        
 16  city     

# **Load**
 - Carregar os dados num DataWareause: SQL & CSV

In [37]:
# VALIDATE
# assert df["valor"].min() >= 0
assert df["Date"].notnull().all()

In [38]:
df_final

Ip                Date Methode  \
0       54.36.149.41 2019-01-22 03:56:14     GET   
1      40.77.167.129 2019-01-22 03:56:17     GET   
2        91.99.72.15 2019-01-22 03:56:17     GET   
3      40.77.167.129 2019-01-22 03:56:17     GET   
4      40.77.167.129 2019-01-22 03:56:18     GET   
...              ...                 ...     ...   
15425   66.249.66.91 2019-01-22 05:47:16     GET   
15426  40.77.167.170 2019-01-22 05:47:16     GET   
15427   66.249.66.91 2019-01-22 05:47:16     GET   
15428  66.249.66.194 2019-01-22 05:47:17     GET   
15429   66.249.66.91 2019-01-22 05:47:17     GET   

                                                     URL  Protocol  Status  \
0      /filter/27-13-%D9%85%DA%AF%D8%A7%D9%BE%DB%8C%D...  HTTP/1.1     200   
1                      /image/14925/productmodel/100x100  HTTP/1.1     200   
2      /product/31893/62100/%D8%B3%D8%B4%D9%88%D8%A7%...  HTTP/1.1     200   
3                      /image/23488/productmodel/150x150  HTTP/1.1     200   
4                      /image/45437/productmodel/150x150  HTTP/1.1     200   
...                                                  ...       ...     ...   
15425  /filter/b481b874b32b67b226b41b136b570b598b180b...  HTTP/1.1     200   
15426                        /filter/b1b36b200b244b615p1  HTTP/1.1     200   
15427  /filter/p19357v134-%D9%88%D8%B2%DB%8C%D8%B1%DB%8C  HTTP/1.1     200   
15428  /m/filter/b1b103b113b135b136b148b168b180b185b1...  HTTP/1.1     200   
15429  /filter/b36b41b598b168b103b614b88b19b194b35b32...  HTTP/1.1     200   

       is_mobile  is_tablet  is_pc  is_bot    browser       os      continent  \
0          False      False  False    True  AhrefsBot    Other         Europe   
1          False      False  False    True    bingbot    Other  North America   
2          False      False   True   False    Firefox  Windows         Europe   
3          False      False  False    True    bingbot    Other  North America   
4          False      False  False    True    bingbot    Other  North America   
...          ...        ...    ...     ...        ...      ...            ...   
15425      False      False  False    True  Googlebot    Other  North America   
15426      False      False  False    True    bingbot    Other  North America   
15427      False      False  False    True  Googlebot    Other  North America   
15428       True      False  False    True  Googlebot  Android  North America   
15429      False      False  False    True  Googlebot    Other  North America   

             country countryCode       regionName           city        lat  \
0             France          FR  Hauts-de-France        Roubaix  50.692400   
1      United States          US         Virginia        Boydton  36.677696   
2            Germany          DE          Bavaria      Nuremberg  49.452700   
3      United States          US         Virginia        Boydton  36.677696   
4      United States          US         Virginia        Boydton  36.677696   
...              ...         ...              ...            ...        ...   
15425  United States          US       California  Mountain View  37.422500   
15426  United States          US         Virginia        Boydton  36.677696   
15427  United States          US       California  Mountain View  37.422500   
15428  United States          US       California  Mountain View  37.422500   
15429  United States          US       California  Mountain View  37.422500   

             lon                    isp                              org  \
0        3.20113                OVH SAS                              OVH   
1      -78.37471  Microsoft Corporation  Microsoft Azure Cloud (eastus2)   
2       11.07830    Hetzner Online GmbH                          Hetzner   
3      -78.37471  Microsoft Corporation  Microsoft Azure Cloud (eastus2)   
4      -78.37471  Microsoft Corporation  Microsoft Azure Cloud (eastus2)   
...          ...                    ...                              ...   
15

In [39]:
df_final.info()

<class 'pandas.core.frame.DataFrame'>
Index: 15249 entries, 0 to 15429
Data columns (total 25 columns):
 #   Column       Non-Null Count  Dtype         
---  ------       --------------  -----         
 0   Ip           15249 non-null  object        
 1   Date         15249 non-null  datetime64[ns]
 2   Methode      15249 non-null  object        
 3   URL          15249 non-null  object        
 4   Protocol     15249 non-null  object        
 5   Status       15249 non-null  int64         
 6   is_mobile    15249 non-null  bool          
 7   is_tablet    15249 non-null  bool          
 8   is_pc        15249 non-null  bool          
 9   is_bot       15249 non-null  bool          
 10  browser      15249 non-null  object        
 11  os           15249 non-null  object        
 12  continent    15249 non-null  object        
 13  country      15249 non-null  object        
 14  countryCode  15249 non-null  object        
 15  regionName   15249 non-null  object        
 16  city     

In [47]:
df_final = df_final.rename(columns={
    'Ip'                : 'Ip',
    'Date'              : 'Data',
    'Methode'           : 'Metodo',
    'URL'               : 'URL',
    'Protocol'          : 'Protocolo',
    'status_code'       : 'Codigo_Status',
    'is_mobile'         : 'E_Mobile',
    'is_tablet'         : 'E_Tablet',
    'is_pc'             : 'E_Pc',
    'is_bot'            : 'E_Bot',
    'browser'           : 'Navegador',
    'os'                : 'Sistema_Operacional',
    'continent'         : 'Continente',
    'country'           : 'Pais',
    'countryCode'       : 'Codigo_Pais',
    'regionName'        : 'Regiao',
    'city'              : 'Cidade',
    'lat'               : 'Latitude',
    'lon'               : 'Longitude',
    'isp'               : 'Isp',
    'org'               : 'Organizacao',
    'as'                : 'As',
    'proxy'             : 'Proxy',
    'hosting'           : 'Hospedagem',
    'query'             : 'Consulta'
})

In [48]:
df_final.to_pickle('log_dw.pkl') # salvando em pkl com todas as formatações bem definidas.

In [49]:
conn = sqlite3.connect('logServidores_web.db')
df_final.to_sql('log', conn, if_exists = 'replace', index = False)

15249